In [2]:
import pickle
import os
from perses.annihilation.rest import RESTTopologyFactory
from perses.annihilation.lambda_protocol import RESTState
from openmmtools.states import SamplerState, ThermodynamicState, CompoundThermodynamicState
from openmmtools import cache, utils
from perses.dispersed.utils import configure_platform
cache.global_context_cache.platform = configure_platform(utils.get_fastest_platform().getName())
from simtk import openmm, unit
import math
from openmmtools.constants import kB
from openmmtools import mcmc, multistate
import argparse
import copy
from perses.dispersed import feptasks
import mdtraj as md
import numpy as np
from perses.app.relative_point_mutation_setup import PointMutationExecutor

from simtk.openmm import app

Desired platform not supported. exception raised: Error initializing CUDA: CUDA_ERROR_NO_DEVICE (100) at /home/conda/feedstock_root/build_artifacts/openmm_1613569706035/work/platforms/cuda/src/CudaContext.cpp:138
conducting subsequent work with the following platform: CPU


In [39]:
# Set up logger
import logging
_logger = logging.getLogger()
_logger.setLevel(logging.INFO)

length = 1
move_length = 1
timestep = 4

outdir = "/data/chodera/zhangi/perses_benchmark/neq/14/66"
resid = 501
t_max = 1200
radius = 0.5


In [40]:
# Load system
prmtop = app.AmberPrmtopFile(os.path.join(outdir, "RBD_ACE2_complex_N501Y.prmtop"))
inpcrd = app.AmberInpcrdFile(os.path.join(outdir, "RBD_ACE2_complex_N501Y.inpcrd"))


In [41]:
pressure = 1.0 * unit.atmospheres
temperature = 310 * unit.kelvin
nonbonded_method = app.PME
constraints = app.HBonds
remove_cm_motion = False
hydrogen_mass = 4.0 * unit.amu  # Using HMR

system = prmtop.createSystem(
    nonbondedMethod=nonbonded_method,
    constraints=constraints,
    temperature=temperature,
    removeCMMotion=remove_cm_motion,
    hydrogenMass=hydrogen_mass,
)

# Add a barostat to the system
system.addForce(openmm.MonteCarloBarostat(pressure, temperature))


4

In [42]:
for res in prmtop.topology.residues():
    print(res, res.id, res.chain.index)

<Residue 0 (ACE) of chain 0> 1 0
<Residue 1 (THR) of chain 0> 2 0
<Residue 2 (ASN) of chain 0> 3 0
<Residue 3 (LEU) of chain 0> 4 0
<Residue 4 (CYS) of chain 0> 5 0
<Residue 5 (PRO) of chain 0> 6 0
<Residue 6 (PHE) of chain 0> 7 0
<Residue 7 (GLY) of chain 0> 8 0
<Residue 8 (GLU) of chain 0> 9 0
<Residue 9 (VAL) of chain 0> 10 0
<Residue 10 (PHE) of chain 0> 11 0
<Residue 11 (NLN) of chain 0> 12 0
<Residue 12 (ALA) of chain 0> 13 0
<Residue 13 (THR) of chain 0> 14 0
<Residue 14 (ARG) of chain 0> 15 0
<Residue 15 (PHE) of chain 0> 16 0
<Residue 16 (ALA) of chain 0> 17 0
<Residue 17 (SER) of chain 0> 18 0
<Residue 18 (VAL) of chain 0> 19 0
<Residue 19 (TYR) of chain 0> 20 0
<Residue 20 (ALA) of chain 0> 21 0
<Residue 21 (TRP) of chain 0> 22 0
<Residue 22 (ASN) of chain 0> 23 0
<Residue 23 (ARG) of chain 0> 24 0
<Residue 24 (LYS) of chain 0> 25 0
<Residue 25 (ARG) of chain 0> 26 0
<Residue 26 (ILE) of chain 0> 27 0
<Residue 27 (SER) of chain 0> 28 0
<Residue 28 (ASN) of chain 0> 29 0
<Res

<Residue 2161 (HOH) of chain 0> 2162 0
<Residue 2162 (HOH) of chain 0> 2163 0
<Residue 2163 (HOH) of chain 0> 2164 0
<Residue 2164 (HOH) of chain 0> 2165 0
<Residue 2165 (HOH) of chain 0> 2166 0
<Residue 2166 (HOH) of chain 0> 2167 0
<Residue 2167 (HOH) of chain 0> 2168 0
<Residue 2168 (HOH) of chain 0> 2169 0
<Residue 2169 (HOH) of chain 0> 2170 0
<Residue 2170 (HOH) of chain 0> 2171 0
<Residue 2171 (HOH) of chain 0> 2172 0
<Residue 2172 (HOH) of chain 0> 2173 0
<Residue 2173 (HOH) of chain 0> 2174 0
<Residue 2174 (HOH) of chain 0> 2175 0
<Residue 2175 (HOH) of chain 0> 2176 0
<Residue 2176 (HOH) of chain 0> 2177 0
<Residue 2177 (HOH) of chain 0> 2178 0
<Residue 2178 (HOH) of chain 0> 2179 0
<Residue 2179 (HOH) of chain 0> 2180 0
<Residue 2180 (HOH) of chain 0> 2181 0
<Residue 2181 (HOH) of chain 0> 2182 0
<Residue 2182 (HOH) of chain 0> 2183 0
<Residue 2183 (HOH) of chain 0> 2184 0
<Residue 2184 (HOH) of chain 0> 2185 0
<Residue 2185 (HOH) of chain 0> 2186 0
<Residue 2186 (HOH) of ch

<Residue 4494 (HOH) of chain 0> 4495 0
<Residue 4495 (HOH) of chain 0> 4496 0
<Residue 4496 (HOH) of chain 0> 4497 0
<Residue 4497 (HOH) of chain 0> 4498 0
<Residue 4498 (HOH) of chain 0> 4499 0
<Residue 4499 (HOH) of chain 0> 4500 0
<Residue 4500 (HOH) of chain 0> 4501 0
<Residue 4501 (HOH) of chain 0> 4502 0
<Residue 4502 (HOH) of chain 0> 4503 0
<Residue 4503 (HOH) of chain 0> 4504 0
<Residue 4504 (HOH) of chain 0> 4505 0
<Residue 4505 (HOH) of chain 0> 4506 0
<Residue 4506 (HOH) of chain 0> 4507 0
<Residue 4507 (HOH) of chain 0> 4508 0
<Residue 4508 (HOH) of chain 0> 4509 0
<Residue 4509 (HOH) of chain 0> 4510 0
<Residue 4510 (HOH) of chain 0> 4511 0
<Residue 4511 (HOH) of chain 0> 4512 0
<Residue 4512 (HOH) of chain 0> 4513 0
<Residue 4513 (HOH) of chain 0> 4514 0
<Residue 4514 (HOH) of chain 0> 4515 0
<Residue 4515 (HOH) of chain 0> 4516 0
<Residue 4516 (HOH) of chain 0> 4517 0
<Residue 4517 (HOH) of chain 0> 4518 0
<Residue 4518 (HOH) of chain 0> 4519 0
<Residue 4519 (HOH) of ch

<Residue 6994 (HOH) of chain 0> 6995 0
<Residue 6995 (HOH) of chain 0> 6996 0
<Residue 6996 (HOH) of chain 0> 6997 0
<Residue 6997 (HOH) of chain 0> 6998 0
<Residue 6998 (HOH) of chain 0> 6999 0
<Residue 6999 (HOH) of chain 0> 7000 0
<Residue 7000 (HOH) of chain 0> 7001 0
<Residue 7001 (HOH) of chain 0> 7002 0
<Residue 7002 (HOH) of chain 0> 7003 0
<Residue 7003 (HOH) of chain 0> 7004 0
<Residue 7004 (HOH) of chain 0> 7005 0
<Residue 7005 (HOH) of chain 0> 7006 0
<Residue 7006 (HOH) of chain 0> 7007 0
<Residue 7007 (HOH) of chain 0> 7008 0
<Residue 7008 (HOH) of chain 0> 7009 0
<Residue 7009 (HOH) of chain 0> 7010 0
<Residue 7010 (HOH) of chain 0> 7011 0
<Residue 7011 (HOH) of chain 0> 7012 0
<Residue 7012 (HOH) of chain 0> 7013 0
<Residue 7013 (HOH) of chain 0> 7014 0
<Residue 7014 (HOH) of chain 0> 7015 0
<Residue 7015 (HOH) of chain 0> 7016 0
<Residue 7016 (HOH) of chain 0> 7017 0
<Residue 7017 (HOH) of chain 0> 7018 0
<Residue 7018 (HOH) of chain 0> 7019 0
<Residue 7019 (HOH) of ch

<Residue 9494 (HOH) of chain 0> 9495 0
<Residue 9495 (HOH) of chain 0> 9496 0
<Residue 9496 (HOH) of chain 0> 9497 0
<Residue 9497 (HOH) of chain 0> 9498 0
<Residue 9498 (HOH) of chain 0> 9499 0
<Residue 9499 (HOH) of chain 0> 9500 0
<Residue 9500 (HOH) of chain 0> 9501 0
<Residue 9501 (HOH) of chain 0> 9502 0
<Residue 9502 (HOH) of chain 0> 9503 0
<Residue 9503 (HOH) of chain 0> 9504 0
<Residue 9504 (HOH) of chain 0> 9505 0
<Residue 9505 (HOH) of chain 0> 9506 0
<Residue 9506 (HOH) of chain 0> 9507 0
<Residue 9507 (HOH) of chain 0> 9508 0
<Residue 9508 (HOH) of chain 0> 9509 0
<Residue 9509 (HOH) of chain 0> 9510 0
<Residue 9510 (HOH) of chain 0> 9511 0
<Residue 9511 (HOH) of chain 0> 9512 0
<Residue 9512 (HOH) of chain 0> 9513 0
<Residue 9513 (HOH) of chain 0> 9514 0
<Residue 9514 (HOH) of chain 0> 9515 0
<Residue 9515 (HOH) of chain 0> 9516 0
<Residue 9516 (HOH) of chain 0> 9517 0
<Residue 9517 (HOH) of chain 0> 9518 0
<Residue 9518 (HOH) of chain 0> 9519 0
<Residue 9519 (HOH) of ch

...

<Residue 89822 (HOH) of chain 0> 89823 0
<Residue 89823 (HOH) of chain 0> 89824 0
<Residue 89824 (HOH) of chain 0> 89825 0
<Residue 89825 (HOH) of chain 0> 89826 0
<Residue 89826 (HOH) of chain 0> 89827 0
<Residue 89827 (HOH) of chain 0> 89828 0
<Residue 89828 (HOH) of chain 0> 89829 0
<Residue 89829 (HOH) of chain 0> 89830 0
<Residue 89830 (HOH) of chain 0> 89831 0
<Residue 89831 (HOH) of chain 0> 89832 0
<Residue 89832 (HOH) of chain 0> 89833 0
<Residue 89833 (HOH) of chain 0> 89834 0
<Residue 89834 (HOH) of chain 0> 89835 0
<Residue 89835 (HOH) of chain 0> 89836 0
<Residue 89836 (HOH) of chain 0> 89837 0
<Residue 89837 (HOH) of chain 0> 89838 0
<Residue 89838 (HOH) of chain 0> 89839 0
<Residue 89839 (HOH) of chain 0> 89840 0
<Residue 89840 (HOH) of chain 0> 89841 0
<Residue 89841 (HOH) of chain 0> 89842 0
<Residue 89842 (HOH) of chain 0> 89843 0
<Residue 89843 (HOH) of chain 0> 89844 0
<Residue 89844 (HOH) of chain 0> 89845 0
<Residue 89845 (HOH) of chain 0> 89846 0
<Residue 89846 (

<Residue 92488 (HOH) of chain 0> 92489 0
<Residue 92489 (HOH) of chain 0> 92490 0
<Residue 92490 (HOH) of chain 0> 92491 0
<Residue 92491 (HOH) of chain 0> 92492 0
<Residue 92492 (HOH) of chain 0> 92493 0
<Residue 92493 (HOH) of chain 0> 92494 0
<Residue 92494 (HOH) of chain 0> 92495 0
<Residue 92495 (HOH) of chain 0> 92496 0
<Residue 92496 (HOH) of chain 0> 92497 0
<Residue 92497 (HOH) of chain 0> 92498 0
<Residue 92498 (HOH) of chain 0> 92499 0
<Residue 92499 (HOH) of chain 0> 92500 0
<Residue 92500 (HOH) of chain 0> 92501 0
<Residue 92501 (HOH) of chain 0> 92502 0
<Residue 92502 (HOH) of chain 0> 92503 0
<Residue 92503 (HOH) of chain 0> 92504 0
<Residue 92504 (HOH) of chain 0> 92505 0
<Residue 92505 (HOH) of chain 0> 92506 0
<Residue 92506 (HOH) of chain 0> 92507 0
<Residue 92507 (HOH) of chain 0> 92508 0
<Residue 92508 (HOH) of chain 0> 92509 0
<Residue 92509 (HOH) of chain 0> 92510 0
<Residue 92510 (HOH) of chain 0> 92511 0
<Residue 92511 (HOH) of chain 0> 92512 0
<Residue 92512 (

<Residue 94988 (HOH) of chain 0> 94989 0
<Residue 94989 (HOH) of chain 0> 94990 0
<Residue 94990 (HOH) of chain 0> 94991 0
<Residue 94991 (HOH) of chain 0> 94992 0
<Residue 94992 (HOH) of chain 0> 94993 0
<Residue 94993 (HOH) of chain 0> 94994 0
<Residue 94994 (HOH) of chain 0> 94995 0
<Residue 94995 (HOH) of chain 0> 94996 0
<Residue 94996 (HOH) of chain 0> 94997 0
<Residue 94997 (HOH) of chain 0> 94998 0
<Residue 94998 (HOH) of chain 0> 94999 0
<Residue 94999 (HOH) of chain 0> 95000 0
<Residue 95000 (HOH) of chain 0> 95001 0
<Residue 95001 (HOH) of chain 0> 95002 0
<Residue 95002 (HOH) of chain 0> 95003 0
<Residue 95003 (HOH) of chain 0> 95004 0
<Residue 95004 (HOH) of chain 0> 95005 0
<Residue 95005 (HOH) of chain 0> 95006 0
<Residue 95006 (HOH) of chain 0> 95007 0
<Residue 95007 (HOH) of chain 0> 95008 0
<Residue 95008 (HOH) of chain 0> 95009 0
<Residue 95009 (HOH) of chain 0> 95010 0
<Residue 95010 (HOH) of chain 0> 95011 0
<Residue 95011 (HOH) of chain 0> 95012 0
<Residue 95012 (

<Residue 97321 (HOH) of chain 0> 97322 0
<Residue 97322 (HOH) of chain 0> 97323 0
<Residue 97323 (HOH) of chain 0> 97324 0
<Residue 97324 (HOH) of chain 0> 97325 0
<Residue 97325 (HOH) of chain 0> 97326 0
<Residue 97326 (HOH) of chain 0> 97327 0
<Residue 97327 (HOH) of chain 0> 97328 0
<Residue 97328 (HOH) of chain 0> 97329 0
<Residue 97329 (HOH) of chain 0> 97330 0
<Residue 97330 (HOH) of chain 0> 97331 0
<Residue 97331 (HOH) of chain 0> 97332 0
<Residue 97332 (HOH) of chain 0> 97333 0
<Residue 97333 (HOH) of chain 0> 97334 0
<Residue 97334 (HOH) of chain 0> 97335 0
<Residue 97335 (HOH) of chain 0> 97336 0
<Residue 97336 (HOH) of chain 0> 97337 0
<Residue 97337 (HOH) of chain 0> 97338 0
<Residue 97338 (HOH) of chain 0> 97339 0
<Residue 97339 (HOH) of chain 0> 97340 0
<Residue 97340 (HOH) of chain 0> 97341 0
<Residue 97341 (HOH) of chain 0> 97342 0
<Residue 97342 (HOH) of chain 0> 97343 0
<Residue 97343 (HOH) of chain 0> 97344 0
<Residue 97344 (HOH) of chain 0> 97345 0
<Residue 97345 (

<Residue 99821 (HOH) of chain 0> 99822 0
<Residue 99822 (HOH) of chain 0> 99823 0
<Residue 99823 (HOH) of chain 0> 99824 0
<Residue 99824 (HOH) of chain 0> 99825 0
<Residue 99825 (HOH) of chain 0> 99826 0
<Residue 99826 (HOH) of chain 0> 99827 0
<Residue 99827 (HOH) of chain 0> 99828 0
<Residue 99828 (HOH) of chain 0> 99829 0
<Residue 99829 (HOH) of chain 0> 99830 0
<Residue 99830 (HOH) of chain 0> 99831 0
<Residue 99831 (HOH) of chain 0> 99832 0
<Residue 99832 (HOH) of chain 0> 99833 0
<Residue 99833 (HOH) of chain 0> 99834 0
<Residue 99834 (HOH) of chain 0> 99835 0
<Residue 99835 (HOH) of chain 0> 99836 0
<Residue 99836 (HOH) of chain 0> 99837 0
<Residue 99837 (HOH) of chain 0> 99838 0
<Residue 99838 (HOH) of chain 0> 99839 0
<Residue 99839 (HOH) of chain 0> 99840 0
<Residue 99840 (HOH) of chain 0> 99841 0
<Residue 99841 (HOH) of chain 0> 99842 0
<Residue 99842 (HOH) of chain 0> 99843 0
<Residue 99843 (HOH) of chain 0> 99844 0
<Residue 99844 (HOH) of chain 0> 99845 0
<Residue 99845 (

In [31]:
# Build REST factory
_logger.info("Generating REST factory")
_logger.info(f"radius:{radius} nm")
# query_indices = [atom.index for atom in list(htf.hybrid_topology.residues)[int(args.resid)].atoms]
for res in prmtop.topology.residues():
    if res.index == 171 and res.chain.index == 0:
        mutated_res = res
query_indices = [atom.index for atom in mutated_res.atoms()]
_logger.info(f"query indices {query_indices}")
positions = unit.quantity.Quantity(
                    value=np.array([list(atom_pos) for atom_pos in inpcrd.positions.value_in_unit_system(unit.md_unit_system)]),
                    unit=unit.nanometers)
traj = md.Trajectory(np.array(positions), md.Topology.from_openmm(prmtop.topology))
solute_atoms = list(traj.topology.select("is_protein"))
rest_atoms = list(md.compute_neighbors(traj, radius, query_indices, haystack_indices=solute_atoms)[0])
_logger.info(f"rest atoms {rest_atoms}")
# factory = RESTTopologyFactory(system, solute_region=rest_atoms)

# _logger.info("Generating REST states")
# # Get REST system
# REST_system = factory.REST_system



INFO:root:Generating REST factory
INFO:root:radius:0.5 nm
INFO:root:query indices [2637, 2638, 2639, 2640, 2641, 2642, 2643, 2644, 2645, 2646, 2647, 2648, 2649, 2650, 2651, 2652, 2653, 2654, 2655, 2656, 2657]
<ipython-input-31-626867a16a63>:15: DeprecationWarning: `np.int` is a deprecated alias for the builtin `int`. To silence this warning, use `int` by itself. Doing this will not modify any behavior and is safe. When replacing `np.int`, you may wish to use e.g. `np.int64` or `np.int32` to specify the precision. If you wish to review your current use, check the release note link for additional information.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations
  rest_atoms = list(md.compute_neighbors(traj, radius, query_indices, haystack_indices=solute_atoms)[0])
INFO:root:rest atoms [1666, 1668, 1725, 2546, 2547, 2550, 2563, 2564, 2565, 2567, 2569, 2570, 2571, 2572, 2573, 2574, 2575, 2576, 2578, 2579, 2580, 2581, 2582

In [32]:
for atom in traj.topology.atoms:
    if atom.index in rest_atoms:
        print(atom.index, atom)

1666 ASN110-OD1
1668 ASN110-HD21
1725 SER114-HG
2546 TYR166-CA
2547 TYR166-HA
2550 TYR166-HB3
2563 TYR166-C
2564 TYR166-O
2565 GLY167-N
2567 GLY167-CA
2569 GLY167-HA3
2570 GLY167-C
2571 GLY167-O
2572 PHE168-N
2573 PHE168-H
2574 PHE168-CA
2575 PHE168-HA
2576 PHE168-CB
2578 PHE168-HB3
2579 PHE168-CG
2580 PHE168-CD1
2581 PHE168-HD1
2582 PHE168-CE1
2583 PHE168-HE1
2590 PHE168-C
2592 GLN169-N
2593 GLN169-H
2594 GLN169-CA
2595 GLN169-HA
2596 GLN169-CB
2597 GLN169-HB2
2598 GLN169-HB3
2599 GLN169-CG
2600 GLN169-HG2
2601 GLN169-HG3
2602 GLN169-CD
2603 GLN169-OE1
2604 GLN169-NE2
2605 GLN169-HE21
2606 GLN169-HE22
2607 GLN169-C
2608 GLN169-O
2609 PRO170-N
2610 PRO170-CD
2611 PRO170-HD2
2616 PRO170-CB
2619 PRO170-CA
2620 PRO170-HA
2621 PRO170-C
2622 PRO170-O
2623 THR171-N
2624 THR171-H
2625 THR171-CA
2626 THR171-HA
2627 THR171-CB
2628 THR171-HB
2629 THR171-CG2
2630 THR171-HG21
2633 THR171-OG1
2634 THR171-HG1
2635 THR171-C
2636 THR171-O
2637 TYR172-N
2638 TYR172-H
2639 TYR172-CA
2640 TYR172-HA
2641 

In [33]:
len(rest_atoms)

176

In [ ]:
# Create states for each replica
n_replicas = 24  # Number of temperature replicas.
T_min = 298.0 * unit.kelvin  # Minimum temperature.
T_max = args.t_max * unit.kelvin  # Maximum temperature.
temperatures = [T_min + (T_max - T_min) * (math.exp(float(i) / float(n_replicas-1)) - 1.0) / (math.e - 1.0)
                for i in range(n_replicas)]

# Create reference thermodynamic state
lambda_zero_alchemical_state = RESTState.from_system(REST_system)
thermostate = ThermodynamicState(REST_system, temperature=T_min)
compound_thermodynamic_state = CompoundThermodynamicState(thermostate, composable_states=[lambda_zero_alchemical_state])

context_cache = cache.ContextCache()



In [ ]:
# Create thermodynamics states
sampler_state =  SamplerState(htf.hybrid_positions, box_vectors=htf.hybrid_system.getDefaultPeriodicBoxVectors())
beta_0 = 1/(kB*T_min)
thermodynamic_state_list = []
sampler_state_list = []
for temperature in temperatures:
    beta_m = 1/(kB*temperature)
    compound_thermodynamic_state_copy = copy.deepcopy(compound_thermodynamic_state)
    compound_thermodynamic_state_copy.set_alchemical_parameters(beta_0, beta_m)
    thermodynamic_state_list.append(compound_thermodynamic_state_copy)

    # now generating a sampler_state for each thermodynamic state, with relaxed positions
    # context, context_integrator = context_cache.get_context(compound_thermodynamic_state_copy)
    feptasks.minimize(compound_thermodynamic_state_copy, sampler_state, max_iterations=0)
    sampler_state_list.append(copy.deepcopy(sampler_state))

from openmmtools.multistate import ReplicaExchangeSampler
import mpiplus
class ReplicaExchangeSampler2(ReplicaExchangeSampler):
    @mpiplus.on_single_node(rank=0, broadcast_result=False, sync_nodes=False)
    @mpiplus.delayed_termination
    def _report_iteration_items(self):
        """
        Sub-function of :func:`_report_iteration` which handles all the actual individual item reporting in a
        sub-class friendly way. The final actions of writing timestamp, last-good-iteration, and syncing
        should be left to the :func:`_report_iteration` and subclasses should extend this function instead
        """
        replica_id = np.where(self._replica_thermodynamic_states == 0)[0][0]
        print("ITERATION: ", self._iteration)
        print("REPLICA THERMOSTATES ", self._replica_thermodynamic_states, type(self._replica_thermodynamic_states))
        print("REPLICA ID ", replica_id, type(replica_id))
        self._reporter.write_sampler_states([self._sampler_states[replica_id]], self._iteration)
        
        self._reporter.write_replica_thermodynamic_states(self._replica_thermodynamic_states, self._iteration)
        self._reporter.write_mcmc_moves(self._mcmc_moves)  # MCMCMoves can store internal statistics.
        self._reporter.write_energies(self._energy_thermodynamic_states, self._neighborhoods, self._energy_unsampled_states,
                                      self._iteration)
        self._reporter.write_mixing_statistics(self._n_accepted_matrix, self._n_proposed_matrix, self._iteration)

# Set up sampler
_logger.setLevel(logging.DEBUG)
_logger.info("About to start repex")
print(f"move steps: {int((move_length*1000)/timestep)}")
print(f"timestep: {timestep} fs")
move = mcmc.LangevinSplittingDynamicsMove(timestep=timestep*unit.femtoseconds, n_steps=int((move_length*1000)/timestep))
simulation = ReplicaExchangeSampler2(mcmc_moves=move, number_of_iterations=length*1000)

# Run t-repex
reporter_file = os.path.join(args.dir, f"{i}_{phase}_{name.lower()}_{length}ns.nc")
reporter = multistate.MultiStateReporter(reporter_file, checkpoint_interval=1)
simulation.create(thermodynamic_states=thermodynamic_state_list,
                  sampler_states=sampler_state_list,
                  storage=reporter)
simulation.run()
